# Solution Optimization Evaluaton Raw TextGrad

In [54]:
import pandas as pd
import textgrad as tg
from textgrad.engine import get_engine
from textgrad.variable import Variable
from textgrad.optimizer import TextualGradientDescent
from textgrad.verifier import TextualVerifier
from textgrad.loss import TextLoss

## Load Datasets

In [55]:
initial_solution = pd.read_csv("csv/initial_solution.csv")
initial_solution

id                                 formatted_question  \
0      2  Answer the following multiple choice question....   
1      4  Answer the following multiple choice question....   
2      8  Answer the following multiple choice question....   
3      1  Answer the following multiple choice question....   
4     22  Answer the following multiple choice question....   
..   ...                                                ...   
407  394  Answer the following multiple choice question....   
408  384  Answer the following multiple choice question....   
409  404  Answer the following multiple choice question....   
410  390  Answer the following multiple choice question....   
411  396  Answer the following multiple choice question....   

                                          raw_solution correct_answer  \
0    Here's how we can determine the number of carb...              A   
1    Maxwell's equations in our universe are:\n\n1....              A   
2    Here's how we can analyze the results and dete...              B   
3    The energy-time uncertainty principle states t...              A   
4    The question asks about the oxidizing power of...              D   
..                                                 ...            ...   
407  The police car is moving towards the wall.  Le...              B   
408  Here's how we can solve this problem:\n\n1. **...              A   
409  The diffraction of electrons by a crystal latt...              A   
410  Here's how we can solve this problem:\n\n1. **...              D   
411  Here's how to solve this problem using conserv...              C   

           source          subject  
0    GPQA-Diamond                -  
1    GPQA-Diamond                -  
2    GPQA-Diamond                -  
3    GPQA-Diamond                -  
4    GPQA-Diamond                -  
..            ...              ...  
407       MMLU-CP  college_physics  
408       MMLU-CP  college_physics  
409       MMLU-CP  college_physics  
410       MMLU-CP  college_physics  
411       MMLU-CP  college_physics  

[412 rows x 6 columns]

In [56]:
# Test size only 50 rows each datasets (Total 150 rows)

df_gpqa = initial_solution[initial_solution['source'] == 'GPQA-Diamond'].head(50)
df_mmlu_ml = initial_solution[initial_solution['source'] == 'MMLU-ML'].head(50)
df_mmlu_cp = initial_solution[initial_solution['source'] == 'MMLU-CP'].head(50)
df_test = pd.concat([df_gpqa, df_mmlu_ml, df_mmlu_cp], ignore_index=True)

df_test

id                                 formatted_question  \
0      2  Answer the following multiple choice question....   
1      4  Answer the following multiple choice question....   
2      8  Answer the following multiple choice question....   
3      1  Answer the following multiple choice question....   
4     22  Answer the following multiple choice question....   
..   ...                                                ...   
145  339  Answer the following multiple choice question....   
146  388  Answer the following multiple choice question....   
147  364  Answer the following multiple choice question....   
148  380  Answer the following multiple choice question....   
149  363  Answer the following multiple choice question....   

                                          raw_solution correct_answer  \
0    Here's how we can determine the number of carb...              A   
1    Maxwell's equations in our universe are:\n\n1....              A   
2    Here's how we can analyze the results and dete...              B   
3    The energy-time uncertainty principle states t...              A   
4    The question asks about the oxidizing power of...              D   
..                                                 ...            ...   
145  The proton is initially accelerated through a ...              D   
146  Einstein's theory of the photoelectric effect ...              D   
147  We are given that the mass of object B is twic...              C   
148  The electric displacement current, denoted by ...              A   
149  A Hermitian operator is equal to its conjugate...              A   

           source          subject  
0    GPQA-Diamond                -  
1    GPQA-Diamond                -  
2    GPQA-Diamond                -  
3    GPQA-Diamond                -  
4    GPQA-Diamond                -  
..            ...              ...  
145       MMLU-CP  college_physics  
146       MMLU-CP  college_physics  
147       MMLU-CP  college_physics  
148       MMLU-CP  college_physics  
149       MMLU-CP  college_physics  

[150 rows x 6 columns]

## Experiment

In [57]:
engine = get_engine("gemini-1.5-pro")
tg.set_backward_engine("gemini-1.5-pro", override=True)

In [58]:
def evaluate_with_raw_textgrad(row_data):
    match = initial_solution[initial_solution["id"] == row_data["id"]]
    if match.empty:
        return None  # or raise error
    formatted_question = match.iloc[0]["formatted_question"]
    result = {
        "id": row_data["id"],
        "raw_solution": row_data["raw_solution"],
        "correct_answer": row_data["correct_answer"],
        "source": row_data["source"],
        "subject": row_data["subject"]
    }
    
    solution = Variable(row_data["raw_solution"],
                    requires_grad=True,
                    role_description=f"Solution to the math question: {formatted_question}")
    loss_system_prompt = Variable("""You will evaluate a solution to a math question. 
                                    Do not attempt to solve it yourself, do not give a solution, 
                                    only identify errors. Be super concise.""",
                                    requires_grad=False,
                                    role_description="system prompt")
    optimizer = TextualGradientDescent([solution])
    loss = TextLoss(loss_system_prompt, engine=engine)
    
    # Iterate 5 times
    for i in range(1, 6):
        optimizer.zero_grad()  # Clean gradients
        loss_result = loss(solution)
        
        loss_result.backward()
        optimizer.step()
        result[f"solution_{i}"] = solution.value

    return result

## Running Evaluation

### Raw TextGrad

In [59]:
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm import tqdm
import time

results = []
start_time = time.time()

with ThreadPoolExecutor(max_workers=64) as executor:
    # Submit all tasks
    futures = [
        executor.submit(evaluate_with_raw_textgrad, row.to_dict()) 
        for _, row in initial_solution.iterrows()
    ]
    
    # Use tqdm for progress tracking
    for future in tqdm(as_completed(futures), total=len(futures), desc="Processing"):
        result = future.result()
        if result is not None:
            results.append(result)

raw_textgrad = pd.DataFrame(results)

print(f"Completed in {time.time() - start_time:.1f} seconds")
raw_textgrad.to_csv('results/raw_textgrad.csv', index=False)

Processing:   0%|          | 0/412 [00:00<?, ?it/s]

["Here is a conversation:\n\n<CONVERSATION><LM_SYSTEM_PROMPT> You will evaluate a solution to a math question. \n                                    Do not attempt to solve it yourself, do not give a solution, \n                                    only identify errors. Be super concise. </LM_SYSTEM_PROMPT>\n\n<LM_INPUT> Maxwell's equations in our universe are:\n\n1. **Gauss's law for electricity:** This relates the divergence of the electric field to the charge density.\n2. **Gauss's law for magnetism:** This relates the divergence of the magnetic field to the magnetic monopole density (which is zero in our universe).\n3. **Faraday's law of induction:** This relates the circulation of the electric field to the time rate of change of the magnetic field.\n4. **Ampère-Maxwell's law:** This relates the circulation of the magnetic field to the current density and the time rate of change of the electric field.\n\nIf magnetic monopoles exist, Gauss's law for magnetism would have to be modifie

Processing:   1%|          | 5/412 [00:13<16:39,  2.45s/it]

['Here is a conversation:\n\n<CONVERSATION><LM_SYSTEM_PROMPT> You will evaluate a solution to a math question. \n                                    Do not attempt to solve it yourself, do not give a solution, \n                                    only identify errors. Be super concise. </LM_SYSTEM_PROMPT>\n\n<LM_INPUT> Here\'s how we can deduce the compound from the NMR data:\n\n1. **Doublet at 7.0 ppm (1H, d, J = 16.0 Hz):** This signal indicates a vinyl proton (proton attached to a double bond). The large coupling constant (J = 16.0 Hz) strongly suggests a *trans* configuration across the double bond.\n\n2. **Signal at 5.5 ppm (1H, dq):** This signal represents another vinyl proton, which is adjacent to both the double bond and a methyl group (hence the dq, doublet of quartets, splitting pattern).\n\n3. **Singlet at 2.1 ppm (3H, s):** This singlet corresponds to a methyl group attached to an electronegative atom, likely an acetate group (CH3CO-).\n\n4. **Doublet at 1.6 ppm (3H, d):*

Processing:   1%|▏         | 6/412 [00:16<17:35,  2.60s/it]

...

["Here is a conversation:\n\n<CONVERSATION><LM_SYSTEM_PROMPT> You will evaluate a solution to a math question. \n                                    Do not attempt to solve it yourself, do not give a solution, \n                                    only identify errors. Be super concise. </LM_SYSTEM_PROMPT>\n\n<LM_INPUT> Here's how to solve this problem using conservation of momentum and energy, noting that the positron and electrons all move in the same direction:\n\n1. **Conservation of momentum:** Initially, the photon has momentum E/c and the electron is at rest. Finally, the two electrons and the positron move with speed v in the photon's initial direction. Thus, the final momentum is 2mv + mv = 3mv. Therefore, E/c = 3mv.\n\n2. **Conservation of energy:** Initially, the total energy is the photon's energy E plus the electron's rest energy mc^2. Finally, the total energy is the sum of the energies of the two electrons and the positron, all moving at speed v. Each particle has energy

Processing: 100%|█████████▉| 411/412 [06:52<00:09,  9.30s/it]

["Here is a conversation:\n\n<CONVERSATION><LM_SYSTEM_PROMPT> You will evaluate a solution to a math question. \n                                    Do not attempt to solve it yourself, do not give a solution, \n                                    only identify errors. Be super concise. </LM_SYSTEM_PROMPT>\n\n<LM_INPUT> Here's how to solve this problem using conservation of momentum and energy, noting that the positron and electrons all move in the same direction with equal speeds:\n\n1. **Conservation of momentum:** Initially, the photon has momentum E/c and the electron is at rest (momentum 0). Finally, the two electrons and one positron each have momentum γmv.  Therefore, E/c = 3γmv, where γ = 1/sqrt(1 - v^2/c^2).\n\n2. **Conservation of energy:** Initially, the total energy is the photon's energy E plus the electron's rest energy mc^2. Finally, the total energy is the sum of the energies of the two electrons and the positron, all moving at speed v. Each particle has energy γmc^2. T

Processing: 100%|██████████| 412/412 [07:02<00:00,  1.03s/it]

Completed in 422.9 seconds
